In [36]:
import pandas as pd
import plotly.express as px
from plotly.subplots import make_subplots
import plotly.graph_objects as go

# Exploratory Data Analysis

In [2]:
df = pd.read_csv('../data_NO2.csv', sep=';')
df['datetime_utc'] = pd.to_datetime(df['datetime_utc'])

display(df.head())
display(df.dtypes)
display(df.describe())
print('Number of nans in each column:')
display(df.apply(lambda col: col.isna().sum(), axis=0))
df.sort_values(by='datetime_utc', inplace=True)

print('Time span:')
print(df.datetime_utc.min().date(), '-', df.datetime_utc.max().date())

datetime_utc  volume_demand  volume_production  spot_price
0 2015-12-31 23:00:00+00:00         4043.0             7818.0       16.39
1 2016-01-01 00:00:00+00:00         4010.0             7694.0       16.04
2 2016-01-01 01:00:00+00:00         3930.0             7437.0       15.74
3 2016-01-01 02:00:00+00:00         3839.0             7120.0       15.57
4 2016-01-01 03:00:00+00:00         3833.0             7041.0       15.47

datetime_utc         datetime64[ns, UTC]
volume_demand                    float64
volume_production                float64
spot_price                       float64
dtype: object

volume_demand  volume_production    spot_price
count   23666.000000       23666.000000  23666.000000
mean     4026.109186        5861.271867     30.891299
std       800.387150        1903.453922      9.601914
min      2490.000000        1082.000000      2.890000
25%      3373.000000        4449.000000     24.180000
50%      3875.000000        5605.000000     29.110000
75%      4648.000000        7411.750000     34.710000
max      6712.000000        9953.000000    114.700000

Number of nans in each column:


datetime_utc         0
volume_demand        0
volume_production    0
spot_price           0
dtype: int64

Time span:
2015-12-31 - 2018-09-13


## Price plots

In [47]:
fig = make_subplots(rows=4, cols=1, subplot_titles=('Spot Price', 
                                    'Demand Volume', 
                                    'Production Volumne', 
                                    'Demand/Production difference'))

fig.append_trace(go.Scatter(
    x=df['datetime_utc'],
    y=df['spot_price'],
), row=1, col=1)

fig.append_trace(go.Scatter(
    x=df['datetime_utc'],
    y=df['volume_demand'],
), row=2, col=1)

fig.append_trace(go.Scatter(
    x=df['datetime_utc'],
    y=df['volume_production'],
), row=3, col=1)

df['prod_dem_diff'] = df['volume_demand']-df['volume_production']
fig.append_trace(go.Scatter(
    x=df['datetime_utc'],
    y=df['prod_dem_diff'],
), row=4, col=1)

fig.update_layout(height=1200)
fig.show()

## Missing data (for lags)

- hours or dates missing??

In [30]:
df['year'] = df['datetime_utc'].dt.year
df['month'] = df['datetime_utc'].dt.month
df['day'] = df['datetime_utc'].dt.day
df['hour'] = df['datetime_utc'].dt.hour
df_hr_missing = df.copy()
df_hr_missing['time_delta'] = df['datetime_utc']-df['datetime_utc'].shift(1)
df_hr_missing['error'] = df_hr_missing['time_delta'] != pd.Timedelta(1,unit='h')
df_hr_missing[df_hr_missing['error']]

datetime_utc  volume_demand  volume_production  spot_price  \
0     2015-12-31 23:00:00+00:00         4043.0             7818.0      16.390   
7273  2016-10-30 01:00:00+00:00         3450.5             3027.0      32.025   
16008 2017-10-29 01:00:00+00:00         3584.5             3890.0      22.325   

       prod_dem_diff  year  month  day  hour  min  minutes      time_delta  \
0            -3775.0  2015     12   31    23    0        0             NaT   
7273           423.5  2016     10   30     1    0        0 0 days 02:00:00   
16008         -305.5  2017     10   29     1    0        0 0 days 02:00:00   

       error  
0       True  
7273    True  
16008   True

### Checking out the variance around these

In [55]:
ids = df_hr_missing[df_hr_missing['error']].index[1:].to_list()
window_size = 5

variable = ['spot_price', 'volume_demand', 'volume_production'][0]

fig = make_subplots(rows=len(ids), cols=1)
for i, id in enumerate(ids):
    rows = df_hr_missing.loc[id-window_size:id+window_size]
    fig.append_trace(go.Scatter(
        x=rows['datetime_utc'],
        y=rows[variable],
    ), row=i+1, col=1)

fig.update_layout(height=300*len(ids), title_text="Stacked Subplots")
fig.show()

This happens because the hours are changed from winter/summer time. Deciding not to fill in these values.

# Price, demand and production through a week

In [65]:
df['week_number'] = df['datetime_utc'].dt.isocalendar().week
df['weekday'] = df['datetime_utc'].dt.dayofweek
df

datetime_utc  volume_demand  volume_production  spot_price  \
0     2015-12-31 23:00:00+00:00         4043.0             7818.0       16.39   
1     2016-01-01 00:00:00+00:00         4010.0             7694.0       16.04   
2     2016-01-01 01:00:00+00:00         3930.0             7437.0       15.74   
3     2016-01-01 02:00:00+00:00         3839.0             7120.0       15.57   
4     2016-01-01 03:00:00+00:00         3833.0             7041.0       15.47   
...                         ...            ...                ...         ...   
23661 2018-09-12 22:00:00+00:00         3399.0             4843.0       50.53   
23662 2018-09-12 23:00:00+00:00         3287.0             4840.0       50.12   
23663 2018-09-13 00:00:00+00:00         3228.0             4769.0       50.12   
23664 2018-09-13 01:00:00+00:00         3274.0             4889.0       50.65   
23665 2018-09-13 02:00:00+00:00         3333.0             5025.0       51.81   

       prod_dem_diff  year  month  day  hour  min  minutes  weekday  \
0            -3775.0  2015     12   31    23    0        0        3   
1            -3684.0  2016      1    1     0    0        0        4   
2            -3507.0  2016      1    1     1    0        0        4   
3            -3281.0  2016      1    1     2    0        0        4   
4            -3208.0  2016      1    1     3    0        0        4   
...              ...   ...    ...  ...   ...  ...      ...      ...   
23661        -1444.0  2018      9   12    22    0        0        2   
23662        -1553.0  2018      9   12    23    0        0        2   
23663        -1541.0  2018      9   13     0    0        0        3   
23664        -1615.0  2018      9   13     1    0        0        3   
23665        -1692.0  2018      9   13     2    0        0        3   

       week_number  week_day  
0               53         3  
1               53         4  
2               53         4  
3               53         4  
4               53         4  
...            ...       ...  
23661           37         2  
23662           37         2  
23663           37         3  
23664           37         3  
23665           37         3  

[23666 rows x 14 columns]

In [104]:
count_per_week = df.groupby(['year', 'week_number']).agg(
    count = ('spot_price', 'count'),
    weekly_avg_price = ('spot_price', 'mean'),
    weekly_avg_dem = ('volume_demand', 'mean'),
    weekly_avg_prod = ('volume_production', 'mean')
).reset_index()
right = count_per_week[count_per_week['count'] == 168].drop('count', axis=1)
weekly = pd.merge(df, right, how='right', on=['year', 'week_number'])
weekly['volume_demand'] = weekly['volume_demand']-weekly['weekly_avg_dem']
weekly['volume_production'] = weekly['volume_production']-weekly['weekly_avg_prod']
weekly['spot_price'] = weekly['spot_price']-weekly['weekly_avg_price']
weekly = weekly.groupby('weekday').agg(
    avg_dem = ('volume_demand', 'mean'),
    avg_prod = ('volume_production', 'mean'),
    avg_price = ('spot_price', 'mean')
).reset_index()

fig = make_subplots(rows=3, cols=1, subplot_titles=('Spot Price', 
                                    'Demand Volume', 
                                    'Production Volumne'))

fig.append_trace(go.Scatter(
    x=weekly['weekday'],
    y=weekly['avg_price'],
), row=1, col=1)

fig.append_trace(go.Scatter(
    x=weekly['weekday'],
    y=weekly['avg_dem'],
), row=2, col=1)

fig.append_trace(go.Scatter(
    x=weekly['weekday'],
    y=weekly['avg_prod'],
), row=3, col=1)

fig.update_layout(height=1200)
fig.show()

Prices are lower on saturdays and sundays



In [112]:
display(df[df['year'] < 2018].groupby('weekday')['spot_price'].mean())

hrly_avgs = df[df['year'] < 2018].groupby('hour')['spot_price'].mean()
fig = px.line(x=[i for i in range(len(hrly_avgs))], y=hrly_avgs)
fig.show()

weekday
0    27.435240
1    27.664671
2    27.548233
3    27.530601
4    27.268159
5    26.064016
6    25.427677
Name: spot_price, dtype: float64